# Modelling

In [11]:
import pandas as pd
pd.set_option('max_colwidth',100)
import numpy as np
import matplotlib.pyplot as plt
import scipy as sp
import seaborn as sns
from sklearn import preprocessing as pp
import pickle
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [2]:
# Logistic Regression
from sklearn.linear_model import LogisticRegressionCV, LogisticRegression, SGDClassifier
from sklearn.model_selection import cross_val_predict, GridSearchCV, train_test_split
from sklearn import metrics
from sklearn.preprocessing import StandardScaler
import xgboost as xgb

In [3]:
X_st_df = pd.read_pickle('./couple_data_predictors')
y_st_df = pd.read_pickle('./couple_data_target')

In [4]:
# Scale the resampled features
Xs_st = StandardScaler().fit_transform(X_st_df)
y_st = y_st_df.values.ravel()

In [5]:
# Training and Test set
X_train, X_test, y_train, y_test = train_test_split(Xs_st, y_st, test_size=0.33, random_state=42)

### Plain Vanilla Logistic Regression

In [9]:
# Plain vanilla logistic regression
lr = LogisticRegression()
train_predicted = cross_val_predict(lr, X_train, y_train, cv=10)
score = metrics.f1_score(y_train, train_predicted)
print('f1 score:', score)
lr.fit(X_train, y_train)
predicted = lr.predict(X_test)
print('LOGREG RESULT:')
print(metrics.classification_report(y_test, predicted, labels=[1,0], target_names=['break up','still together']))

f1 score: 0.855662472243
LOGREG RESULT:
                precision    recall  f1-score   support

      break up       0.86      0.84      0.85       356
still together       0.83      0.85      0.84       328

   avg / total       0.85      0.85      0.85       684



In [10]:
# Get top 10 coefficients
lr_coef = pd.DataFrame({
    'coef':lr.coef_.ravel(),
    'mag':np.abs(lr.coef_.ravel()),
    'pred':X_st_df.columns
})
lr_coef.sort_values(by=['mag'], ascending=False, inplace=True)
lr_coef.head(10)

coef       mag                                     pred
120 -1.227879  1.227879                        coresident[T.Yes]
3   -0.920787  0.920787  ppeducat[T.bachelor's degree or higher]
130 -0.857349  0.857349                 how_long_ago_first_cohab
60  -0.793168  0.793168          marriage_count[T.never married]
56  -0.716937  0.716937         partner_politic_view[T.democrat]
61  -0.687461  0.687461                   marriage_count[T.once]
118 -0.665304  0.665304                       married[T.married]
77  -0.590546  0.590546                  met_partner_work[T.yes]
57  -0.515090  0.515090      partner_politic_view[T.independent]
2   -0.511848  0.511848                 ppeducat[T.some college]

### Ridge Logistic Regression

In [11]:
# Ridge logistic regression
lr_ridge = LogisticRegressionCV(penalty='l2', Cs=200, cv=10, scoring='f1')
lr_ridge.fit(X_train, y_train)
train_predicted = lr_ridge.predict(X_train)
score = metrics.f1_score(y_train, train_predicted)
print('f1 score:', score)
ridge_predicted = lr_ridge.predict(X_test)
print('RIDGE LOGREG RESULT:')
print(metrics.classification_report(y_test, ridge_predicted, labels=[1,0], target_names=['break up','still together']))

f1 score: 0.882525697504
RIDGE LOGREG RESULT:
                precision    recall  f1-score   support

      break up       0.87      0.85      0.86       356
still together       0.84      0.86      0.85       328

   avg / total       0.86      0.86      0.86       684



In [12]:
# Get top 10 coefficients
lr_ridge_coef = pd.DataFrame({
    'coef':lr_ridge.coef_.ravel(),
    'mag':np.abs(lr_ridge.coef_.ravel()),
    'pred':X_st_df.columns
})
lr_ridge_coef.sort_values(by=['mag'], ascending=False, inplace=True)
lr_ridge_coef.head(10)

coef       mag                             pred
120 -0.146106  0.146106                coresident[T.Yes]
118 -0.135905  0.135905               married[T.married]
131 -0.086926  0.086926            how_long_relationship
129 -0.086562  0.086562      how_long_ago_first_romantic
128 -0.077820  0.077820           how_long_ago_first_met
60  -0.071768  0.071768  marriage_count[T.never married]
119 -0.061931  0.061931     parental_approval[T.approve]
17   0.059383  0.059383         ppmarit[T.never married]
9   -0.058549  0.058549                  pphhhead[T.yes]
121 -0.053300  0.053300                            ppage

### Lasso Logistic Regression

In [14]:
# Lasso Logistic Regression
lr_lasso = LogisticRegressionCV(penalty='l1', solver='liblinear', Cs=100, cv=10)
lr_lasso.fit(X_train, y_train)
train_predicted = lr_lasso.predict(X_train)
score = metrics.f1_score(y_train, train_predicted)
print('f1 score:', score)
lasso_predicted = lr_lasso.predict(X_test)
print('LASSO LOGREG RESULT:')
print(metrics.classification_report(y_test, lasso_predicted, labels=[1,0], target_names=['break up','still together']))

f1 score: 0.894187779434
LASSO LOGREG RESULT:
                precision    recall  f1-score   support

      break up       0.88      0.86      0.87       356
still together       0.85      0.87      0.86       328

   avg / total       0.86      0.86      0.86       684



In [15]:
# Get top 10 coefficients
lr_lasso_coef = pd.DataFrame({
    'coef':lr_lasso.coef_.ravel(),
    'mag':np.abs(lr_lasso.coef_.ravel()),
    'pred':X_st_df.columns
})
lr_lasso_coef.sort_values(by=['mag'], ascending=False, inplace=True)
lr_lasso_coef.head(10)

coef       mag                                               pred
120 -1.004958  1.004958                                  coresident[T.Yes]
118 -0.636460  0.636460                                 married[T.married]
130 -0.469215  0.469215                           how_long_ago_first_cohab
119 -0.366960  0.366960                       parental_approval[T.approve]
76  -0.309651  0.309651  parent_alive[T.neither father nor mother are a...
77  -0.306350  0.306350                            met_partner_work[T.yes]
121 -0.290343  0.290343                                              ppage
131 -0.263679  0.263679                              how_long_relationship
46  -0.263077  0.263077                                pprace_white[T.yes]
3   -0.249756  0.249756            ppeducat[T.bachelor's degree or higher]

### GridSearch Logistic Regression

In [6]:
# Gridsearch for Ridge and Lasso Logistic Regression, optimize C

parameters = {
    'penalty':['l1','l2'],
    'solver':['liblinear'],
    'C':np.logspace(-5,0,100)
}

print ("GRID SEARCH:")
lr_grid_search = GridSearchCV(LogisticRegression(), parameters, cv=10, verbose=0)
lr_grid_search.fit(X_train, y_train)
print ("Best parameters set:")
print('f1 score:', lr_grid_search.best_score_)
lr_best_parameters = lr_grid_search.best_estimator_.get_params()
for param_name in sorted(parameters.keys()):
    print ("\t%s: %r" % (param_name, lr_best_parameters[param_name]))
print ("-----------------------------------------")
print ("-----------------------------------------")
print ("GRIDSEARCHCV LOGREG RESULT:")
clf = lr_grid_search.best_estimator_
lr_gs_predicted = clf.predict(X_test)
print(metrics.classification_report(y_test, lr_gs_predicted, labels=[1,0], target_names=['break up','still together']))

GRID SEARCH:
Best parameters set:
f1 score: 0.882395382395
	C: 0.10974987654930568
	penalty: 'l1'
	solver: 'liblinear'
-----------------------------------------
-----------------------------------------
GRIDSEARCHCV LOGREG RESULT:
                precision    recall  f1-score   support

      break up       0.87      0.86      0.87       356
still together       0.85      0.87      0.86       328

   avg / total       0.86      0.86      0.86       684



In [12]:
# Get top 10 coefficients
lr_gs_coef = pd.DataFrame({
    'coef':clf.coef_.ravel(),
    'mag':np.abs(clf.coef_.ravel()),
    'pred':X_st_df.columns
})
lr_gs_coef.sort_values(by=['mag'], ascending=False, inplace=True)
lr_gs_coef.head(10)

coef       mag                                                 pred
120 -0.993028  0.993028                                    coresident[T.Yes]
118 -0.642351  0.642351                                   married[T.married]
130 -0.437784  0.437784                             how_long_ago_first_cohab
119 -0.364599  0.364599                         parental_approval[T.approve]
76  -0.305227  0.305227  parent_alive[T.neither father nor mother are alive]
77  -0.302348  0.302348                              met_partner_work[T.yes]
121 -0.288203  0.288203                                                ppage
131 -0.273547  0.273547                                how_long_relationship
46  -0.253192  0.253192                                  pprace_white[T.yes]
3   -0.245582  0.245582              ppeducat[T.bachelor's degree or higher]

### GridSearch SGDClassifier

In [18]:
# Gridsearch SGDclassifier with log loss and optimal learning rate

sgd_parameters = {
    'learning_rate': ['optimal'],
    'loss':['log','hinge'],
    'penalty': ['l1','l2','elasticnet'],
    'alpha': np.logspace(-10,5,100),
    'l1_ratio': np.logspace(-1,0,20)
}

print ("GRID SEARCH:")
sgd_grid_search = GridSearchCV(SGDClassifier(max_iter=10000, tol=0.0001), sgd_parameters, cv=10, verbose=0)
sgd_grid_search.fit(X_train, y_train)
print ("Best parameters set:")
print('f1 score:', sgd_grid_search.best_score_)
sgd_best_parameters = sgd_grid_search.best_estimator_.get_params()
for param_name in sorted(sgd_parameters.keys()):
    print ("\t%s: %r" % (param_name, sgd_best_parameters[param_name]))
print ("-----------------------------------------")
print ("-----------------------------------------")
print ("GRIDSEARCHCV SGDCLASSIFIER RESULT:")
sgd_clf = sgd_grid_search.best_estimator_
sgd_predicted = sgd_clf.predict(X_test)
print(metrics.classification_report(y_test, sgd_predicted, labels=[1,0], target_names=['break up','still together']))

GRID SEARCH:


/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

...

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
/Users/david.yan/anaconda/lib/python3.6/site-pac

Best parameters set:
f1 score: 0.878977736293
	alpha: 0.021544346900318867
	l1_ratio: 0.42813323987193935
	learning_rate: 'optimal'
	loss: 'log'
	penalty: 'elasticnet'
-----------------------------------------
-----------------------------------------
GRIDSEARCHCV SGDCLASSIFIER RESULT:
                precision    recall  f1-score   support

      break up       0.88      0.85      0.86       356
still together       0.84      0.87      0.85       328

   avg / total       0.86      0.86      0.86       684



In [19]:
# Get top 10 coefficients
sgd_coef = pd.DataFrame({
    'coef':sgd_clf.coef_.ravel(),
    'mag':np.abs(sgd_clf.coef_.ravel()),
    'pred':X_st_df.columns
})
sgd_coef.sort_values(by=['mag'], ascending=False, inplace=True)
sgd_coef.head(10)

coef       mag                                               pred
120 -0.830305  0.830305                                  coresident[T.Yes]
118 -0.624808  0.624808                                 married[T.married]
119 -0.332172  0.332172                       parental_approval[T.approve]
76  -0.272295  0.272295  parent_alive[T.neither father nor mother are a...
77  -0.254003  0.254003                            met_partner_work[T.yes]
3   -0.240814  0.240814            ppeducat[T.bachelor's degree or higher]
46  -0.225401  0.225401                                pprace_white[T.yes]
131 -0.207649  0.207649                              how_long_relationship
121 -0.201148  0.201148                                              ppage
129 -0.195829  0.195829                        how_long_ago_first_romantic

### GridSearch XGBoost Classifier

In [20]:
# Reference link: https://www.kaggle.com/phunter/xgboost-with-gridsearchcv
# Credit to Shize's R code and the python re-implementation

xgb_model = xgb.XGBClassifier()

#brute force scan for all parameters, here are the tricks
#usually max_depth is 6,7,8
#learning rate is around 0.05, but small changes may make big diff
#tuning min_child_weight subsample colsample_bytree can have 
#much fun of fighting against overfit 
#n_estimators is how many round of boosting
#finally, ensemble xgboost with multiple seeds may reduce variance
parameters = {'nthread':[4], #when use hyperthread, xgboost may become slower
              'objective':['binary:logistic'],
              'learning_rate': [0.05], #so called `eta` value
              'max_depth': [6,7,8],
              'min_child_weight': [11],
              'silent': [1],
              'subsample': [0.8],
              'colsample_bytree': [0.7],
              'n_estimators': [1000], #number of trees, change it to 1000 for better results
              'missing':[-999],
              'seed': [65]}

xgb_clf = GridSearchCV(xgb_model, parameters, n_jobs=5, scoring='f1', verbose=0, refit=True, cv=10)

xgb_clf.fit(X_train, y_train)

best_parameters, score, _ = max(xgb_clf.grid_scores_, key=lambda x: x[1])
print('f1 score:', score)
for param_name in sorted(best_parameters.keys()):
    print("%s: %r" % (param_name, best_parameters[param_name]))
    
print ("-----------------------------------------")
print ("-----------------------------------------")
print ("GRIDSEARCHCV XGBCLASSIFIER RESULT:")
xgb_predicted = xgb_clf.best_estimator_.predict(X_test)
print(metrics.classification_report(y_test, xgb_predicted, labels=[1,0], target_names=['break up','still together']))

f1 score: 0.889563987042
colsample_bytree: 0.7
learning_rate: 0.05
max_depth: 7
min_child_weight: 11
missing: -999
n_estimators: 1000
nthread: 4
objective: 'binary:logistic'
seed: 65
silent: 1
subsample: 0.8
-----------------------------------------
-----------------------------------------
GRIDSEARCHCV XGBCLASSIFIER RESULT:
                precision    recall  f1-score   support

      break up       0.89      0.87      0.88       356
still together       0.87      0.88      0.87       328

   avg / total       0.88      0.88      0.88       684



/Users/david.yan/anaconda/lib/python3.6/site-packages/sklearn/model_selection/_search.py:761: DeprecationWarning: The grid_scores_ attribute was deprecated in version 0.18 in favor of the more elaborate cv_results_ attribute. The grid_scores_ attribute will not be available from 0.20
  DeprecationWarning)


In [21]:
# Get top 10 coefficients
xgb_featimpt = pd.DataFrame({
    'importance':xgb_clf.best_estimator_.feature_importances_,
    'pred':X_st_df.columns
})
xgb_featimpt = xgb_featimpt[xgb_featimpt.importance > 0]
xgb_featimpt.sort_values(by=['importance'], ascending=False, inplace=True)
xgb_featimpt.head(10)

importance                         pred
121    0.088318                        ppage
127    0.061758           distancemoved_10mi
132    0.056575               age_difference
128    0.051393       how_long_ago_first_met
130    0.048586     how_long_ago_first_cohab
122    0.046210                        hhinc
129    0.045131  how_long_ago_first_romantic
135    0.044267                partner_yrsed
134    0.038868             respondent_yrsed
125    0.038221     relatives_seen_per_month

In [22]:
print(metrics.accuracy_score(y_test, xgb_predicted))

0.87865497076


In [23]:
xgboost_df = X_st_df[xgb_featimpt.pred.tolist()]
xgboost_df.to_pickle('./couple_data_xgboost_predictors')